In [ ]:
import pandas as pd
import chess.pgn
import io
import re
import logging
import os

logging.basicConfig(level=logging.INFO)

def parse_game_data(input_data):
    games = re.split(r'(?=\[Event)', input_data.strip())
    valid_time_controls = {
        "Bullet": ["60+0", "60+1", "120+1"],
        "Blitz": ["180+0", "180+2", "300+0", "300+3"],
        "Rapid": ["600+0", "600+5", "900+10"],
        "Classical": ["1800+0", "1800+20"]
    }

    all_moves_data = []

    for game_text in games:
        pgn = io.StringIO(game_text)
        game = chess.pgn.read_game(pgn)

        if not game:
            continue

        headers = game.headers
        necessary_fields = ["Event", "Site", "Date", "Round", "White", "Black", "Result"]

        if not all(field in headers for field in necessary_fields):
            logging.warning("Skipping game due to missing necessary fields")
            continue

        result = headers.get("Result", "")
        if result not in {"1-0", "0-1", "1/2-1/2"}:
            logging.warning("Skipping game due to invalid result")
            continue

        time_control = headers.get("TimeControl", "")
        format_type = next((format_name for format_name, controls in valid_time_controls.items() if time_control in controls), None)

        if format_type is None:
            logging.warning("Skipping game due to invalid time control")
            continue

        white_elo = headers.get("WhiteElo", "")
        black_elo = headers.get("BlackElo", "")
        termination = headers.get("Termination", "")

        white_elo = int(white_elo)
        black_elo = int(black_elo)

        if abs(white_elo - black_elo) > 75:
            logging.warning("Skipping game due to Elo difference greater than 75")
            continue

        base_time, increment = map(int, time_control.split('+'))

        board = game.board()
        node = game
        move_number = 1

        mainline_moves = list(game.mainline_moves())
        if not mainline_moves:
            continue

        prev_white_time = base_time
        prev_black_time = base_time

        for move in mainline_moves:
            fen_before_move = board.fen()
            game_move = board.san(move)
            board.push(move)

            move_comment = node.comment
            clock_time_match = re.search(r'\[%clk (\d+):(\d+):(\d+)\]', move_comment)

            if move_number == 1:  # First move scenario
                clock_time = prev_white_time
            elif clock_time_match:
                hours, minutes, seconds = map(int, clock_time_match.groups())
                clock_time = hours * 3600 + minutes * 60 + seconds
            else:
                clock_time = 0

            if move_number % 2 == 1:  # White's move
                think_time = prev_white_time - clock_time
                prev_white_time = clock_time + increment
            else:  # Black's move
                think_time = prev_black_time - clock_time
                prev_black_time = clock_time + increment

            phase = categorize_position(board.fen())

            move_data = {
                "Format": format_type,
                "Result": result,
                "White Elo": white_elo,
                "Black Elo": black_elo,
                "Termination": termination,
                "Time Control": time_control,
                "Move": game_move,
                "Think Time": think_time,
                "White Clock Time": prev_white_time,
                "Black Clock Time": prev_black_time,
                "Phase": phase,
                "FEN Before the move": fen_before_move
            }
            all_moves_data.append(move_data)
            move_number += 1

            if node.variations:
                node = node.variation(0)
            else:
                break

    return pd.DataFrame(all_moves_data)

def categorize_position(fen):
    board = chess.Board(fen)
    piece_count = len(board.piece_map())
    major_pieces = sum(2 for piece in board.piece_map().values() if piece.symbol().upper() in 'QR')
    minor_pieces = sum(1 for piece in board.piece_map().values() if piece.symbol().upper() in 'BN')
    pawn_count = sum(1 for piece in board.piece_map().values() if piece.symbol().upper() == 'P')
    king_safety = all(board.piece_at(square) and board.piece_at(square).symbol().upper() == 'K' for square in [chess.E1, chess.E8])
    piece_activity = sum(1 for move in board.legal_moves)
    pawn_structure = sum(1 for square in chess.SQUARES if board.piece_at(square) and board.piece_at(square).symbol().upper() == 'P' and (square in chess.SQUARES[8:16] or square in chess.SQUARES[48:56]))
    developed_pieces = sum(1 for square in chess.SQUARES if board.piece_at(square) and board.piece_at(square).symbol().upper() in 'BNQR' and (square not in chess.SQUARES[0:16] and square not in chess.SQUARES[48:64]))
    
    if piece_count > 20 and pawn_structure > 4 and king_safety and developed_pieces < 4:
        return "Opening"
    elif (major_pieces + minor_pieces >= 5) or developed_pieces >= 4:
        return "Middlegame"
    else:
        return "Endgame"

def read_chunk(file_path, chunk_size=10*1024*1024):
    with open(file_path, 'rb') as file:
        while True:
            data = file.read(chunk_size)
            if not data:
                break
            last_event_index = data.rfind(b'[Event')
            if last_event_index == -1:
                continue
            yield data[:last_event_index].decode('utf-8')
            file.seek(last_event_index, os.SEEK_CUR)

file_path = 'Data/chess_games_1400.pgn'

for chunk in read_chunk(file_path):
    df_games = parse_game_data(chunk)

    if df_games.empty:
        continue

    if not os.path.isfile('DataFrames/game-data_1400.csv'):
        df_games.to_csv('DataFrames/game-data_1400.csv', index=False)
    else:
        df_games.to_csv('DataFrames/game-data_1400.csv', mode='a', header=False, index=False)

ERROR:chess.pgn:illegal san: 'd5' in rnbqkbnr/pppppppp/8/8/8/8/PPPPPPPP/RNBQKBNR w KQkq - 0 1 while parsing <Game at 0x2705be5c890 ('?' vs. '?', '????.??.??' at '?')>


ERROR:chess.pgn:illegal san: 'Rf1' in rnbqkbnr/pppppppp/8/8/8/8/PPPPPPPP/RNBQKBNR w KQkq - 0 1 while parsing <Game at 0x27013225b50 ('?' vs. '?', '????.??.??' at '?')>


ERROR:chess.pgn:illegal san: 'Bxd2' in rnbqkbnr/pppppppp/8/8/8/8/PPPPPPPP/RNBQKBNR w KQkq - 0 1 while parsing <Game at 0x27043eb0c50 ('?' vs. '?', '????.??.??' at '?')>


ERROR:chess.pgn:illegal san: 'Nc6' in rnbqkbnr/pppppppp/8/8/8/8/PPPPPPPP/RNBQKBNR w KQkq - 0 1 while parsing <Game at 0x270124efe10 ('?' vs. '?', '????.??.??' at '?')>


ERROR:chess.pgn:illegal san: 'a5' in rnbqkbnr/pppppppp/8/8/8/8/PPPPPPPP/RNBQKBNR w KQkq - 0 1 while parsing <Game at 0x27013a520d0 ('?' vs. '?', '????.??.??' at '?')>


...

ERROR:chess.pgn:illegal san: 'Bxg3' in rnbqkbnr/pppppppp/8/8/8/8/PPPPPPPP/RNBQKBNR w KQkq - 0 1 while parsing <Game at 0x27063856410 ('?' vs. '?', '????.??.??' at '?')>


ERROR:chess.pgn:illegal san: 'Bxa3' in rnbqkbnr/pppppppp/8/8/8/8/PPPPPPPP/RNBQKBNR w KQkq - 0 1 while parsing <Game at 0x270657b0e90 ('?' vs. '?', '????.??.??' at '?')>


ERROR:chess.pgn:illegal san: 'Bg5' in rnbqkbnr/pppppppp/8/8/8/8/PPPPPPPP/RNBQKBNR w KQkq - 0 1 while parsing <Game at 0x27013488b90 ('?' vs. '?', '????.??.??' at '?')>


ERROR:chess.pgn:illegal san: 'Be7' in rnbqkbnr/pppppppp/8/8/8/8/PPPPPPPP/RNBQKBNR w KQkq - 0 1 while parsing <Game at 0x27006f4ff10 ('?' vs. '?', '????.??.??' at '?')>


ERROR:chess.pgn:illegal san: 'Re1' in rnbqkbnr/pppppppp/8/8/8/8/PPPPPPPP/RNBQKBNR w KQkq - 0 1 while parsing <Game at 0x2705ba38150 ('?' vs. '?', '????.??.??' at '?')>


In [10]:
df_games.count

<bound method DataFrame.count of         Format Result  White Elo  Black Elo   Termination Time Control  Move  \
0        Blitz    1-0       1426       1500        Normal        300+0    d4   
1        Blitz    1-0       1426       1500        Normal        300+0    d5   
2        Blitz    1-0       1426       1500        Normal        300+0    e3   
3        Blitz    1-0       1426       1500        Normal        300+0   Nc6   
4        Blitz    1-0       1426       1500        Normal        300+0   Bd3   
...        ...    ...        ...        ...           ...          ...   ...   
223349  Bullet    1-0       1436       1439  Time forfeit         60+0  Kxg4   
223350  Bullet    1-0       1436       1439  Time forfeit         60+0   Kg7   
223351  Bullet    1-0       1436       1439  Time forfeit         60+0    b5   
223352  Bullet    1-0       1436       1439  Time forfeit         60+0   Kh6   
223353  Bullet    1-0       1436       1439  Time forfeit         60+0    b6   

      